In [1]:
pip install requests

Note: you may need to restart the kernel to use updated packages.


In [2]:
asteroids_data = []
target = 10000
API_KEY = "CrZpBBrPoPEKL903s4ItNc5OELyDOxKiC8pPhoqY"

import requests

url = f"https://api.nasa.gov/neo/rest/v1/feed?start_date=2025-05-01&end_date=2025-05-08&api_key={API_KEY}"

while len(asteroids_data) < target:
    response = requests.get(url)
    data = response.json()

    neo_data = data.get('near_earth_objects', {})
    for date, ast_details in neo_data.items():
        for ast in ast_details:
            cad = next((cad for cad in ast.get('close_approach_data', []) if cad.get('orbiting_body') == 'Earth'), None)

            if cad:
                asteroids_data.append(dict(
                    id=int(ast['id']),
                    neo_reference_id=int(ast['neo_reference_id']),
                    name=ast['name'],
                    magnitude=ast['absolute_magnitude_h'],
                    dia_min=ast['estimated_diameter']['kilometers']['estimated_diameter_min'],
                    dia_max=ast['estimated_diameter']['kilometers']['estimated_diameter_max'],
                    is_potentially_hazardous_asteroid=bool(ast['is_potentially_hazardous_asteroid']),
                    close_approach_date=cad['close_approach_date'],
                    relative_velocity_kph=cad['relative_velocity']['kilometers_per_hour'],
                    miss_distance_km=cad['miss_distance']['kilometers'],
                    miss_distance_lunar=cad['miss_distance']['lunar'],
                    miss_distance_au=cad['miss_distance']['astronomical'],
                    orbiting_body=cad['orbiting_body']
                ))

            if len(asteroids_data) >= target:
                break
        if len(asteroids_data) >= target:
            break

    # Try to move to the next page (note: feed endpoint doesn't support pagination beyond 7 days)
    next_url = data.get('links', {}).get('next')
    if not next_url:
        print("No more pages to fetch.")
        break
    url = next_url

In [3]:
len(asteroids_data)

10000

In [4]:
!pip install pymysql

In [5]:
import pymysql

# Step 1: Connect without selecting a database
connection = pymysql.connect(
    host='localhost',
    user='root',
    password='Arvi@3194',
    cursorclass=pymysql.cursors.DictCursor
)

try:
    with connection.cursor() as cursor:
        # Step 2: Create the database if it doesn't exist
        cursor.execute("CREATE DATABASE IF NOT EXISTS MINI_NASA")
        print("Database 'MINI_NASA' ensured.")

finally:
    connection.close()

# Step 3: Now connect to the newly created database
connection = pymysql.connect(
    host='localhost',
    user='root',
    password='Arvi@3194',
    database='MINI_NASA',
    cursorclass=pymysql.cursors.DictCursor
)

cursor = connection.cursor()
print("Connected to 'MINI_NASA' database.")



Database 'MINI_NASA' ensured.
Connected to 'MINI_NASA' database.


In [6]:
cursor.execute("""
CREATE TABLE IF NOT EXISTS asteroids (
    id VARCHAR(255),
    name VARCHAR(255),
    absolute_magnitude FLOAT,
    dia_min FLOAT,
    dia_max FLOAT,
    is_potentially_hazardous_asteroid BOOLEAN
)
""")

connection.commit()
print("✅ Table 'asteroids' created successfully.")

✅ Table 'asteroids' created successfully.


In [11]:
len(asteroids_data)

10000

In [8]:

cursor = connection.cursor()

insert = """
INSERT INTO asteroids (id, name, absolute_magnitude, dia_min, dia_max,is_potentially_hazardous_asteroid)
VALUES (%s, %s, %s, %s, %s,%s)
"""

for a in asteroids_data:
    values = (a['id'], a['name'], a['magnitude'], a['dia_min'], a['dia_max'],a['is_potentially_hazardous_asteroid'])
    cursor.execute(insert, values)

connection.commit()
print("✅ Data inserted into 'asteroids' table.")

✅ Data inserted into 'asteroids' table.


In [12]:
cursor.execute("""
CREATE TABLE IF NOT EXISTS close_approach (
    neo_reference_id INT,
    close_approach_date DATE,
    relative_velocity_kmph FLOAT,
    astronomical_au FLOAT,
    miss_distance_km FLOAT,
    miss_distance_lunar FLOAT,
    orbiting_body VARCHAR(255)
)
""")

connection.commit()
print("✅ Table 'close_approach' created successfully.")

✅ Table 'close_approach' created successfully.


In [16]:
# Ensure you have the cursor
cursor = connection.cursor()

# SQL insert query
insert_query = """
INSERT INTO close_approach (
    neo_reference_id,
    close_approach_date,
    relative_velocity_kmph,
    astronomical_au,
    miss_distance_km,
    miss_distance_lunar,
    orbiting_body
) VALUES (%s, %s, %s, %s, %s, %s, %s)
"""

# Sample loop assuming you have a list of dictionaries
for ca in asteroids_data:
    values = (
        ca['neo_reference_id'],
        ca['close_approach_date'],
        ca['relative_velocity_kph'],
        ca['miss_distance_au'],
        ca['miss_distance_km'],
        ca['miss_distance_lunar'],
        ca['orbiting_body']
    )
    cursor.execute(insert_query, values)

# Commit the changes
connection.commit()
print("✅ Data inserted into 'close_approach' table.")


✅ Data inserted into 'close_approach' table.


In [19]:
# Ensure you have the cursor
cursor = connection.cursor()

query = """
SELECT
    a.name,
    a.id,
    COUNT(ca.neo_reference_id) AS approach_count
FROM
    asteroids a
LEFT JOIN
    close_approach ca ON ca.neo_reference_id = a.id
GROUP BY
    a.id, a.name
ORDER BY
    approach_count DESC;
"""

cursor.execute(query)
results = cursor.fetchall()

for row in results:
    print(f"Asteroid {row['name']} (ID: {row['id']}) approached Earth {row['approach_count']} times")

Asteroid (2023 QB2) (ID: 54377574) approached Earth 64 times
Asteroid (2018 RO5) (ID: 3829424) approached Earth 49 times
Asteroid (2015 XF261) (ID: 3736497) approached Earth 49 times
Asteroid (2022 QB37) (ID: 54300837) approached Earth 49 times
Asteroid (2015 YA) (ID: 3736807) approached Earth 49 times
Asteroid (2006 TL) (ID: 3348144) approached Earth 36 times
Asteroid (2010 VB) (ID: 3550117) approached Earth 36 times
Asteroid (2022 EO) (ID: 54248949) approached Earth 36 times
Asteroid (2014 QZ295) (ID: 3683472) approached Earth 36 times
Asteroid (2023 RC) (ID: 54379768) approached Earth 36 times
Asteroid (2024 GE3) (ID: 54433568) approached Earth 36 times
Asteroid 141531 (2002 GB) (ID: 2141531) approached Earth 36 times
Asteroid (2016 CN248) (ID: 3744561) approached Earth 36 times
Asteroid (2022 UE3) (ID: 54317205) approached Earth 36 times
Asteroid (2022 YS5) (ID: 54336914) approached Earth 36 times
Asteroid (2024 UQ11) (ID: 54496852) approached Earth 36 times
Asteroid (2023 RN7) (ID

In [23]:
query = """
SELECT neo_reference_id, COUNT(*) AS approach_count
FROM close_approach
GROUP BY neo_reference_id;
"""

cursor.execute(query)
results = cursor.fetchall()

for row in results:
    print(f"Asteroid ID: {row['neo_reference_id']} → Approached {row['approach_count']} times")

Asteroid ID: 3373919 → Approached 4 times
Asteroid ID: 54110077 → Approached 1 times
Asteroid ID: 54138303 → Approached 2 times
Asteroid ID: 54144240 → Approached 4 times
Asteroid ID: 54421069 → Approached 1 times
Asteroid ID: 54527149 → Approached 1 times
Asteroid ID: 54527284 → Approached 1 times
Asteroid ID: 54527292 → Approached 1 times
Asteroid ID: 54527390 → Approached 1 times
Asteroid ID: 54527597 → Approached 1 times
Asteroid ID: 54528735 → Approached 1 times
Asteroid ID: 54528916 → Approached 1 times
Asteroid ID: 3485809 → Approached 1 times
Asteroid ID: 3634275 → Approached 1 times
Asteroid ID: 3774574 → Approached 1 times
Asteroid ID: 54073370 → Approached 1 times
Asteroid ID: 54135427 → Approached 1 times
Asteroid ID: 54142841 → Approached 1 times
Asteroid ID: 54161068 → Approached 2 times
Asteroid ID: 54317869 → Approached 1 times
Asteroid ID: 54335008 → Approached 1 times
Asteroid ID: 54352572 → Approached 2 times
Asteroid ID: 54439998 → Approached 3 times
Asteroid ID: 54

In [24]:
cursor = connection.cursor()

query = """
SELECT neo_reference_id, AVG(relative_velocity_kmph) AS avg_velocity
FROM close_approach
GROUP BY neo_reference_id;
"""

cursor.execute(query)
results = cursor.fetchall()

for row in results:
    print(f"Asteroid ID: {row['neo_reference_id']} → Average Velocity: {row['avg_velocity']:.2f} km/h")

Asteroid ID: 3373919 → Average Velocity: 60167.74 km/h
Asteroid ID: 54110077 → Average Velocity: 48556.40 km/h
Asteroid ID: 54138303 → Average Velocity: 58390.29 km/h
Asteroid ID: 54144240 → Average Velocity: 80174.55 km/h
Asteroid ID: 54421069 → Average Velocity: 16418.46 km/h
Asteroid ID: 54527149 → Average Velocity: 39868.48 km/h
Asteroid ID: 54527284 → Average Velocity: 36354.09 km/h
Asteroid ID: 54527292 → Average Velocity: 22514.94 km/h
Asteroid ID: 54527390 → Average Velocity: 48137.51 km/h
Asteroid ID: 54527597 → Average Velocity: 23747.77 km/h
Asteroid ID: 54528735 → Average Velocity: 51293.14 km/h
Asteroid ID: 54528916 → Average Velocity: 81718.21 km/h
Asteroid ID: 3485809 → Average Velocity: 59644.52 km/h
Asteroid ID: 3634275 → Average Velocity: 58251.59 km/h
Asteroid ID: 3774574 → Average Velocity: 82611.36 km/h
Asteroid ID: 54073370 → Average Velocity: 26192.47 km/h
Asteroid ID: 54135427 → Average Velocity: 75509.07 km/h
Asteroid ID: 54142841 → Average Velocity: 132900.33 

In [25]:
query = """
SELECT neo_reference_id, MAX(relative_velocity_kmph) AS max_velocity
FROM close_approach
GROUP BY neo_reference_id
ORDER BY max_velocity DESC
LIMIT 10;
"""

cursor.execute(query)
results = cursor.fetchall()

# Print results
for row in results:
    print(f"Asteroid ID: {row['neo_reference_id']} → Max Velocity: {row['max_velocity']} km/h")

Asteroid ID: 2504181 → Max Velocity: 186136.0 km/h
Asteroid ID: 2394130 → Max Velocity: 169787.0 km/h
Asteroid ID: 3639550 → Max Velocity: 163863.0 km/h
Asteroid ID: 54239841 → Max Velocity: 162471.0 km/h
Asteroid ID: 54203006 → Max Velocity: 160285.0 km/h
Asteroid ID: 3472374 → Max Velocity: 159112.0 km/h
Asteroid ID: 54194346 → Max Velocity: 157682.0 km/h
Asteroid ID: 3409988 → Max Velocity: 151120.0 km/h
Asteroid ID: 3588900 → Max Velocity: 149521.0 km/h
Asteroid ID: 3837511 → Max Velocity: 149438.0 km/h


In [26]:
query = """
SELECT MONTH(close_approach_date) AS month, COUNT(*) AS total_approaches
FROM close_approach
GROUP BY MONTH(close_approach_date)
ORDER BY total_approaches DESC
LIMIT 1;
"""
cursor.execute(query)
print(cursor.fetchone())

{'month': 5, 'total_approaches': 1233}


In [27]:
query = """
SELECT neo_reference_id, relative_velocity_kmph
FROM close_approach
ORDER BY relative_velocity_kmph DESC
LIMIT 1;
"""
cursor.execute(query)
print(cursor.fetchone())

{'neo_reference_id': 2504181, 'relative_velocity_kmph': 186136.0}


In [30]:
query = """
SELECT id, name, dia_max
FROM asteroids
ORDER BY dia_max DESC;
"""
cursor.execute(query)
for row in cursor.fetchall():
    print(row)

{'id': '2000433', 'name': '433 Eros (A898 PA)', 'dia_max': 49.2085}
{'id': '2066146', 'name': '66146 (1998 TU3)', 'dia_max': 7.98068}
{'id': '2004953', 'name': '4953 (1990 MU)', 'dia_max': 6.22358}
{'id': '2138205', 'name': '138205 (2000 EZ148)', 'dia_max': 5.70217}
{'id': '2138205', 'name': '138205 (2000 EZ148)', 'dia_max': 5.70217}
{'id': '2001620', 'name': '1620 Geographos (1951 RA)', 'dia_max': 5.24856}
{'id': '2001620', 'name': '1620 Geographos (1951 RA)', 'dia_max': 5.24856}
{'id': '2137427', 'name': '137427 (1999 TF211)', 'dia_max': 5.20044}
{'id': '2085818', 'name': '85818 (1998 XM4)', 'dia_max': 4.89824}
{'id': '2001943', 'name': '1943 Anteros (1973 EC)', 'dia_max': 4.32554}
{'id': '2105140', 'name': '105140 (2000 NL10)', 'dia_max': 4.22708}
{'id': '2105140', 'name': '105140 (2000 NL10)', 'dia_max': 4.22708}
{'id': '2005863', 'name': '5863 Tara (1983 RB)', 'dia_max': 4.03683}
{'id': '2005863', 'name': '5863 Tara (1983 RB)', 'dia_max': 4.03683}
{'id': '2006063', 'name': '6063 J

In [31]:
query = """
SELECT neo_reference_id, close_approach_date, miss_distance_km
FROM close_approach
ORDER BY neo_reference_id, close_approach_date;
"""
cursor.execute(query)
for row in cursor.fetchall():
    print(row)


{'neo_reference_id': 2000433, 'close_approach_date': datetime.date(2025, 11, 30), 'miss_distance_km': 59487200.0}
{'neo_reference_id': 2001620, 'close_approach_date': datetime.date(2026, 2, 9), 'miss_distance_km': 70749700.0}
{'neo_reference_id': 2001620, 'close_approach_date': datetime.date(2026, 8, 12), 'miss_distance_km': 25497100.0}
{'neo_reference_id': 2001865, 'close_approach_date': datetime.date(2025, 11, 11), 'miss_distance_km': 67882600.0}
{'neo_reference_id': 2001865, 'close_approach_date': datetime.date(2026, 11, 14), 'miss_distance_km': 47982200.0}
{'neo_reference_id': 2001865, 'close_approach_date': datetime.date(2027, 1, 17), 'miss_distance_km': 57759200.0}
{'neo_reference_id': 2001943, 'close_approach_date': datetime.date(2026, 5, 30), 'miss_distance_km': 19771400.0}
{'neo_reference_id': 2002100, 'close_approach_date': datetime.date(2025, 8, 12), 'miss_distance_km': 25866000.0}
{'neo_reference_id': 2002101, 'close_approach_date': datetime.date(2025, 8, 19), 'miss_distanc

In [32]:
query = """
SELECT a.name, c.close_approach_date, c.miss_distance_km
FROM asteroids a
JOIN close_approach c ON a.id = c.neo_reference_id
WHERE (a.id, c.miss_distance_km) IN (
    SELECT neo_reference_id, MIN(miss_distance_km)
    FROM close_approach
    GROUP BY neo_reference_id
);
"""
cursor.execute(query)
for row in cursor.fetchall():
    print(row)

{'name': '(2021 CR1)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 69098800.0}
{'name': '(2021 GT16)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 31465000.0}
{'name': '(2024 BF)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 3635350.0}
{'name': '(2025 GT1)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 4308270.0}
{'name': '(2025 HE1)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 12766400.0}
{'name': '(2025 HN1)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 13368400.0}
{'name': '(2025 HF2)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 20306700.0}
{'name': '(2025 HP3)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 28340900.0}
{'name': '(2025 JB)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 199575.0}
{'name': '(2025 JF)', 'close_approach_date': datetime.date(2

In [33]:
query = """
SELECT DISTINCT neo_reference_id
FROM close_approach
WHERE relative_velocity_kmph > 50000;
"""
cursor.execute(query)
for row in cursor.fetchall():
    print(row)

{'neo_reference_id': 3373919}
{'neo_reference_id': 54138303}
{'neo_reference_id': 54144240}
{'neo_reference_id': 54528735}
{'neo_reference_id': 54528916}
{'neo_reference_id': 3485809}
{'neo_reference_id': 3634275}
{'neo_reference_id': 3774574}
{'neo_reference_id': 54135427}
{'neo_reference_id': 54142841}
{'neo_reference_id': 54317869}
{'neo_reference_id': 54335008}
{'neo_reference_id': 3180147}
{'neo_reference_id': 3670293}
{'neo_reference_id': 3748562}
{'neo_reference_id': 3831479}
{'neo_reference_id': 3841721}
{'neo_reference_id': 54135432}
{'neo_reference_id': 54139086}
{'neo_reference_id': 54239841}
{'neo_reference_id': 54317171}
{'neo_reference_id': 54528918}
{'neo_reference_id': 3465236}
{'neo_reference_id': 3841713}
{'neo_reference_id': 54278174}
{'neo_reference_id': 54289654}
{'neo_reference_id': 3883096}
{'neo_reference_id': 54017159}
{'neo_reference_id': 54051050}
{'neo_reference_id': 54054611}
{'neo_reference_id': 54203700}
{'neo_reference_id': 54527596}
{'neo_reference_id':

In [34]:
query = """
SELECT MONTH(close_approach_date) AS month, COUNT(*) AS count
FROM close_approach
GROUP BY MONTH(close_approach_date)
ORDER BY month;
"""
cursor.execute(query)
for row in cursor.fetchall():
    print(row)


{'month': 1, 'count': 743}
{'month': 2, 'count': 712}
{'month': 3, 'count': 780}
{'month': 4, 'count': 737}
{'month': 5, 'count': 1233}
{'month': 6, 'count': 982}
{'month': 7, 'count': 957}
{'month': 8, 'count': 708}
{'month': 9, 'count': 748}
{'month': 10, 'count': 914}
{'month': 11, 'count': 765}
{'month': 12, 'count': 721}


In [35]:
query = """
SELECT id, name, absolute_magnitude
FROM asteroids
ORDER BY absolute_magnitude ASC
LIMIT 1;
"""
cursor.execute(query)
print(cursor.fetchone())

{'id': '2000433', 'name': '433 Eros (A898 PA)', 'absolute_magnitude': 10.41}


In [36]:
query = """
SELECT neo_reference_id, close_approach_date, miss_distance_lunar
FROM close_approach
WHERE miss_distance_lunar < 1;
"""
cursor.execute(query)
for row in cursor.fetchall():
    print(row)


{'neo_reference_id': 54528735, 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_lunar': 0.518955}
{'neo_reference_id': 54528916, 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_lunar': 0.451765}
{'neo_reference_id': 54528737, 'close_approach_date': datetime.date(2025, 5, 8), 'miss_distance_lunar': 0.953021}
{'neo_reference_id': 54528737, 'close_approach_date': datetime.date(2025, 5, 8), 'miss_distance_lunar': 0.953021}
{'neo_reference_id': 54532864, 'close_approach_date': datetime.date(2025, 5, 21), 'miss_distance_lunar': 0.29936}
{'neo_reference_id': 54533161, 'close_approach_date': datetime.date(2025, 5, 21), 'miss_distance_lunar': 0.363499}
{'neo_reference_id': 54533098, 'close_approach_date': datetime.date(2025, 5, 22), 'miss_distance_lunar': 0.379938}
{'neo_reference_id': 54533318, 'close_approach_date': datetime.date(2025, 5, 22), 'miss_distance_lunar': 0.955938}
{'neo_reference_id': 54533007, 'close_approach_date': datetime.date(2025, 5, 23), 'mi

In [38]:
query = """
SELECT neo_reference_id, close_approach_date, astronomical_au
FROM close_approach
WHERE astronomical_au < 0.05
ORDER BY astronomical_au ASC;
"""

cursor.execute(query)
results = cursor.fetchall()

# Print the results
for row in results:
    print(f"Asteroid ID: {row['neo_reference_id']} | Date: {row['close_approach_date']} | Distance: {row['astronomical_au']} AU")

Asteroid ID: 54532864 | Date: 2025-05-21 | Distance: 0.000769563 AU
Asteroid ID: 54533161 | Date: 2025-05-21 | Distance: 0.000934444 AU
Asteroid ID: 54533098 | Date: 2025-05-22 | Distance: 0.000976705 AU
Asteroid ID: 54533098 | Date: 2025-05-22 | Distance: 0.000976705 AU
Asteroid ID: 54533501 | Date: 2025-05-26 | Distance: 0.00108328 AU
Asteroid ID: 54528916 | Date: 2025-05-01 | Distance: 0.00116135 AU
Asteroid ID: 54533007 | Date: 2025-05-23 | Distance: 0.00129008 AU
Asteroid ID: 54528735 | Date: 2025-05-01 | Distance: 0.00133407 AU
Asteroid ID: 3634154 | Date: 2026-04-14 | Distance: 0.00174152 AU
Asteroid ID: 54533422 | Date: 2025-05-23 | Distance: 0.00186922 AU
Asteroid ID: 54533415 | Date: 2025-05-28 | Distance: 0.00227077 AU
Asteroid ID: 54528737 | Date: 2025-05-08 | Distance: 0.00244993 AU
Asteroid ID: 54528737 | Date: 2025-05-08 | Distance: 0.00244993 AU
Asteroid ID: 54533318 | Date: 2025-05-22 | Distance: 0.00245742 AU
Asteroid ID: 54533318 | Date: 2025-05-22 | Distance: 0.0024

In [39]:
query = """
        SELECT a.id, a.name, ca.close_approach_date, ca.miss_distance_km
        FROM asteroids a
        JOIN close_approach ca ON a.id = ca.neo_reference_id
        ORDER BY ca.miss_distance_km ASC
        LIMIT 10;
        """
cursor.execute(query)
results = cursor.fetchall()
for row in results:
    print(row)


{'id': '54532864', 'name': '(2025 KF)', 'close_approach_date': datetime.date(2025, 5, 21), 'miss_distance_km': 115125.0}
{'id': '54533161', 'name': '(2025 KF2)', 'close_approach_date': datetime.date(2025, 5, 21), 'miss_distance_km': 139791.0}
{'id': '54533098', 'name': '(2025 KS1)', 'close_approach_date': datetime.date(2025, 5, 22), 'miss_distance_km': 146113.0}
{'id': '54533098', 'name': '(2025 KS1)', 'close_approach_date': datetime.date(2025, 5, 22), 'miss_distance_km': 146113.0}
{'id': '54533098', 'name': '(2025 KS1)', 'close_approach_date': datetime.date(2025, 5, 22), 'miss_distance_km': 146113.0}
{'id': '54533098', 'name': '(2025 KS1)', 'close_approach_date': datetime.date(2025, 5, 22), 'miss_distance_km': 146113.0}
{'id': '54533501', 'name': '(2025 KQ4)', 'close_approach_date': datetime.date(2025, 5, 26), 'miss_distance_km': 162057.0}
{'id': '54528916', 'name': '(2025 JF)', 'close_approach_date': datetime.date(2025, 5, 1), 'miss_distance_km': 173735.0}
{'id': '54533007', 'name': 

In [41]:
query = """
        SELECT a.id, a.name, ca.close_approach_date, ca.relative_velocity_kmph
        FROM asteroids a
        JOIN close_approach ca ON a.id = ca.neo_reference_id
        ORDER BY ca.relative_velocity_kmph DESC
        LIMIT 1;
        """
cursor.execute(query)
result = cursor.fetchone()
print(result)

{'id': '2504181', 'name': '504181 (2006 TC)', 'close_approach_date': datetime.date(2025, 10, 12), 'relative_velocity_kmph': 186136.0}


In [42]:
query = """
        SELECT AVG((dia_min + dia_max) / 2) AS avg_diameter
        FROM asteroids;
        """
cursor.execute(query)
result = cursor.fetchone()
print(result)

{'avg_diameter': 0.16261006927570562}


In [43]:
query = """
        SELECT orbiting_body, COUNT(*) AS approach_count
        FROM close_approach
        GROUP BY orbiting_body
        ORDER BY approach_count DESC;
        """
cursor.execute(query)
results = cursor.fetchall()
for row in results:
 print(row)

{'orbiting_body': 'Earth', 'approach_count': 10000}


In [45]:
query= """
        SELECT a.id, a.name, COUNT(ca.neo_reference_id) AS approach_count
        FROM asteroids a
        JOIN close_approach ca ON a.id = ca.neo_reference_id
        GROUP BY a.id, a.name
        HAVING approach_count > 1;
        """
cursor.execute(query)
results = cursor.fetchall()
for row in results:
    print(row)

{'id': '3373919', 'name': '(2007 GW4)', 'approach_count': 16}
{'id': '54138303', 'name': '(2021 GT16)', 'approach_count': 4}
{'id': '54144240', 'name': '(2021 JZ2)', 'approach_count': 16}
{'id': '54161068', 'name': '(2021 MD)', 'approach_count': 4}
{'id': '54352572', 'name': '(2023 FC6)', 'approach_count': 4}
{'id': '54439998', 'name': '(2024 JM2)', 'approach_count': 9}
{'id': '3468431', 'name': '(2009 SA100)', 'approach_count': 4}
{'id': '54317171', 'name': '(2022 UW1)', 'approach_count': 4}
{'id': '3465236', 'name': '(2009 OS5)', 'approach_count': 4}
{'id': '54216314', 'name': '(2021 VH2)', 'approach_count': 4}
{'id': '54278174', 'name': '(2022 JP)', 'approach_count': 9}
{'id': '54397455', 'name': '(2023 UR3)', 'approach_count': 16}
{'id': '54430725', 'name': '(2024 ET3)', 'approach_count': 25}
{'id': '3348144', 'name': '(2006 TL)', 'approach_count': 36}
{'id': '54017159', 'name': '(2020 JN3)', 'approach_count': 4}
{'id': '54203700', 'name': '(2021 TR3)', 'approach_count': 4}
{'id': 

In [ ]:
query = """
        SELECT a.id, a.name, ca.close_approach_date, ca.miss_distance_km
        FROM asteroids a
        JOIN close_approach ca ON a.id = ca.id
        WHERE ca.close_approach_date >= CURDATE() - INTERVAL 1 YEAR
        ORDER BY ca.close_approach_date DESC;
        """
cursor.execute(query)
results = cursor.fetchall()
for row in results:
    print(row)

In [46]:
query = """
        SELECT id, name, absolute_magnitude, dia_min, dia_max
        FROM asteroids
        ORDER BY absolute_magnitude ASC
        LIMIT 5;
        """
cursor.execute(query)
results = cursor.fetchall()
for row in results:
    print(row)

{'id': '2000433', 'name': '433 Eros (A898 PA)', 'absolute_magnitude': 10.41, 'dia_min': 22.0067, 'dia_max': 49.2085}
{'id': '2066146', 'name': '66146 (1998 TU3)', 'absolute_magnitude': 14.36, 'dia_min': 3.56907, 'dia_max': 7.98068}
{'id': '2004953', 'name': '4953 (1990 MU)', 'absolute_magnitude': 14.9, 'dia_min': 2.78327, 'dia_max': 6.22358}
{'id': '2138205', 'name': '138205 (2000 EZ148)', 'absolute_magnitude': 15.09, 'dia_min': 2.55009, 'dia_max': 5.70217}
{'id': '2138205', 'name': '138205 (2000 EZ148)', 'absolute_magnitude': 15.09, 'dia_min': 2.55009, 'dia_max': 5.70217}


In [47]:
query = """
        SELECT id, name, dia_max
        FROM asteroids
        ORDER BY dia_max DESC
        LIMIT 1;
        """
cursor.execute(query)
result = cursor.fetchone()
print(result)

{'id': '2000433', 'name': '433 Eros (A898 PA)', 'dia_max': 49.2085}


In [48]:
query = """
        SELECT orbiting_body, AVG(miss_distance_km) AS avg_miss_distance_km
        FROM close_approach
        GROUP BY orbiting_body
        ORDER BY avg_miss_distance_km ASC;
        """
cursor.execute(query)
results = cursor.fetchall()
for row in results:
    print(row)

{'orbiting_body': 'Earth', 'avg_miss_distance_km': 42139242.096045315}
